<span id="hello-world" />

# ハローワールド



<details>
  <summary><b>パッケージ・バージョン</b></summary>

  このページのコードは、以下の要件に基づいて開発された。
  これらのバージョンまたは新しいバージョンの使用をお勧めします。

  ```
  qiskit[all]~=2.1.1
  qiskit-ibm-runtime~=0.40.1
  ```
</details>



この例には2つの部分がある。 まず簡単な量子プログラムを作成し、量子プロセッシング・ユニット（QPU）で実行する。  実際の量子研究においては、より堅牢なプログラムが必要となるため、第2節 （[大量の量子ビットへのスケール](#scale-to-large-numbers-of-qubits) ）では、単純なプログラムをユーティリティ・レベルまでスケールアップする。



<span id="before-you-begin" />

## 始める前に

[IBM Cloud® を使用するためのセットアップ](/docs/guides/cloud-setup)手順を含む、 [インストールとセットアップの](/docs/guides/install-qiskit)手順に従ってください

IBM Quantum® Platformのドキュメントにあるコード例は、 [Jupyter](https://jupyter.org/install) ノートブックを使用して開発された。  例に沿って進めるには、 [ローカル](/docs/guides/install-qiskit#local-jupyter)または[オンラインで](/docs/guides/online-lab-environments) Jupyterノートブックを実行する環境をセットアップすることをお勧めします 推奨される追加視覚化サポート (`'qiskit[visualization]'`) を必ずインストールしてください。この例の後半では、 `matplotlib` パッケージも必要です。

量子コンピューティング全般について学ぶには、 IBM Quantum Learningの [Basics of quantum informationコースを](/learning/courses/basics-of-quantum-information)ご覧ください。

IBM® は量子コンピューティングの責任ある発展に尽力している。 IBM、責任ある量子[コンピューティングとインクルーシブ・テクノロジーに関する](/docs/responsible-quantum-computing)トピックで、責任ある量子の原則をご確認ください。



<span id="create-and-run-a-simple-quantum-program" />

## 簡単な量子プログラムを作成し、実行する



Qiskitパターンを使って量子プログラムを書くための4つのステップは以下の通り：

1.  問題を量子ネイティブ形式にマップする。

2.  回路とオペレーターを最適化する。

3.  量子プリミティブ関数を使用して実行します。

4.  結果を分析します。

<span id="step-1-map-the-problem-to-a-quantum-native-format" />

### ステップ1. 問題を量子ネイティブ形式にマップする

量子プログラムでは、 *量子回路は*量子命令を表現するネイティブフォーマットであり、 *演算*子は測定される観測量を表す。 回路を作成する場合、通常は新しいオブジェクトを作成し、それに順番に命令を追加していきます。 [`QuantumCircuit`](/docs/api/qiskit/qiskit.circuit.QuantumCircuit#quantumcircuit-class) オブジェクトを作成し、それに順番に命令を追加していきます。



次のコード・セルは、2つの量子ビットが互いに完全にエンタングルされた状態である*ベル状態を*生成する回路を作成する。

<Admonition type="note" title="注：ビット順序">
  Qiskit SDKはLSb 0ビットナンバリングを使用しており、 $n^{th}$ の桁は値 $1 \ll n$ または $2^n$。詳細については、 [Qiskit SDKのビット順序の](/docs/guides/bit-ordering)トピックを参照してください。
</Admonition>



In [1]:
from qiskit import QuantumCircuit
from qiskit.quantum_info import SparsePauliOp
from qiskit.transpiler import generate_preset_pass_manager
from qiskit_ibm_runtime import EstimatorV2 as Estimator

# Create a new circuit with two qubits
qc = QuantumCircuit(2)

# Add a Hadamard gate to qubit 0
qc.h(0)

# Perform a controlled-X gate on qubit 1, controlled by qubit 0
qc.cx(0, 1)

# Return a drawing of the circuit using MatPlotLib ("mpl").
# These guides are written by using Jupyter notebooks, which
# display the output of the last line of each cell.
# If you're running this in a script, use `print(qc.draw())` to
# print a text drawing.
qc.draw("mpl")

<Image src="/docs/images/tutorials/hello-world/extracted-outputs/930ca3b6-0.svg" alt="Output of the previous code cell" />

を参照のこと。 [`QuantumCircuit`](/docs/api/qiskit/qiskit.circuit.QuantumCircuit#quantumcircuit-class) を参照のこと。



量子回路を作成する際には、実行後にどのようなデータを返したいかも考慮しなければならない。 Qiskitはデータを返すために2つの方法を提供します：あなたが測定することを選択した量子ビットのセットに対する確率分布を得ることができ、または観測可能なものの期待値を得ることができます。 [Qiskitプリミティブを](/docs/guides/get-started-with-primitives)使用して、これら2つの方法のいずれかで回路を測定するためにワークロードを準備します（ [ステップ](#step-3-execute-using-the-quantum-primitives) 3で詳しく説明します）。

この例では、 `qiskit.quantum_info` サブモジュールを使って期待値を測定しています。このサブモジュールは、演算子（量子状態を変化させる作用や過程を表すのに使われる数学的オブジェクト）を使って指定します。 次のコード・セルは、6つの2量子ビット・パウリ演算子を作成する： `IZ` `IX`, `ZI`, `XI`, `ZZ`, and `XX`.



In [2]:
# Set up six different observables.

observables_labels = ["IZ", "IX", "ZI", "XI", "ZZ", "XX"]
observables = [SparsePauliOp(label) for label in observables_labels]

<Admonition type="note" title="演算子の表記">
  ここで、 `ZZ` 演算子のようなものは、テンソル積 $Z\otimes Z$ の省略形である。これは、量子ビット1上のZと量子ビット0上のZを一緒に測定し、量子ビット1と量子ビット0間の相関に関する情報を得ることを意味する。 このような期待値は通常、 $\langle Z_1 Z_0 \rangle$ と表記される。

  もし状態がもつれるなら、 $\langle Z_1 Z_0 \rangle$ の測定値は、 $\langle I_1 \otimes Z_0 \rangle \langle Z_1 \otimes I_0 \rangle$ の測定値とは異なるはずである。上述の回路によって作られた特定のもつれ状態の場合、 $\langle Z_1 Z_0 \rangle$ の測定値は1になり、 $\langle I_1 \otimes Z_0 \rangle \langle Z_1 \otimes I_0 \rangle$ の測定値は0になるはずである。
</Admonition>



<span id="optimize" />

<span id="step-2-optimize-the-circuits-and-operators" />

### ステップ2. 回路とオペレーターの最適化

デバイス上で回路を実行する場合、回路が含む命令セットを最適化し、回路全体の深さ（おおよその命令数）を最小化することが重要である。 これにより、エラーやノイズの影響を低減し、可能な限り最高の結果を得ることができます。 さらに、回路の命令はバックエンド・デバイスの[命令セット・アーキテクチャ（ISA](/docs/guides/transpile#instruction-set-architecture) ）に準拠し、デバイスの基底ゲートと量子ビットの接続性を考慮しなければならない。

以下のコードでは、ジョブを投入する実デバイスをインスタンス化し、バックエンドのISAに合わせて回路と観測値を変換している。 [認証情報を保存して](/docs/guides/cloud-setup)いる必要があります



In [3]:
from qiskit_ibm_runtime import QiskitRuntimeService

service = QiskitRuntimeService()

backend = service.least_busy(simulator=False, operational=True)

# Convert to an ISA circuit and layout-mapped observables.
pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
isa_circuit = pm.run(qc)

isa_circuit.draw("mpl", idle_wires=False)

<Image src="/docs/images/tutorials/hello-world/extracted-outputs/9a901271-0.svg" alt="Output of the previous code cell" />

<span id="step-3-execute-using-the-quantum-primitives" />

### ステップ3． 量子プリミティブを使って実行する

量子コンピューターはランダムな結果を出すことができるので、通常は回路を何度も走らせて出力のサンプルを集める。 `Estimator` 。 `Estimator` は2つの[プリミティブの](/docs/guides/get-started-with-primitives)うちの1つで、もう1つは量子コンピューターからデータを取得するために使用できる `Sampler`。  これらのオブジェクトは `run()`[ プリミティブ統合ブロック ( PUB ) を使用して、回路、観測可能量、およびパラメータ (該当する場合) の選択を実行する方法。](/docs/guides/primitives#sampler)



In [4]:
# Construct the Estimator instance.

estimator = Estimator(mode=backend)
estimator.options.resilience_level = 1
estimator.options.default_shots = 5000

mapped_observables = [
    observable.apply_layout(isa_circuit.layout) for observable in observables
]

# One pub, with one circuit to run against five different observables.
job = estimator.run([(isa_circuit, mapped_observables)])

# Use the job ID to retrieve your job data later
print(f">>> Job ID: {job.job_id()}")

>>> Job ID: d2qkdds65eic73blka9g


ジョブが投入された後、現在のpythonインスタンス内でジョブが完了するまで待つか、 `job_id` 、後でデータを取得することができます。  (詳しくは[ジョブの取得のセクションを](/docs/guides/monitor-job#retrieve-job-results-at-a-later-time)参照）

ジョブが完了したら、ジョブの `result()` 。



In [5]:
# This is the result of the entire submission.  You submitted one Pub,
# so this contains one inner result (and some metadata of its own).
job_result = job.result()

# This is the result from our single pub, which had six observables,
# so contains information on all six.
pub_result = job.result()[0]

<Admonition type="note" title="別の方法：シミュレーターを使って例を実行する">
  量子プログラムを実機で実行する場合、ワークロードは実行前にキューで待機しなければならない。 時間を節約するために、次のコードを使用して、この小さなワークロードを [`fake_provider`](../api/qiskit-ibm-runtime/fake-provider)Qiskit Runtime ローカル・テスト・モードで実行する。 これは小さな回路でのみ可能であることに注意。 次のセクションで規模を拡大する際には、実機を使用する必要がある。

  ```python

  # Use the following code instead if you want to run on a simulator:

  from qiskit_ibm_runtime.fake_provider import FakeFez
  backend = FakeFez()
  estimator = Estimator(backend)

  # Convert to an ISA circuit and layout-mapped observables.

  pm = generate_preset_pass_manager(backend=backend, optimization_level=1)
  isa_circuit = pm.run(qc)
  mapped_observables = [
      observable.apply_layout(isa_circuit.layout) for observable in observables
  ]

  job = estimator.run([(isa_circuit, mapped_observables)])
  result = job.result()

  # This is the result of the entire submission.  You submitted one Pub,
  # so this contains one inner result (and some metadata of its own).

  job_result = job.result()

  # This is the result from our single pub, which had five observables,
  # so contains information on all five.

  pub_result = job.result()[0]
  ```
</Admonition>



<span id="step-4-analyze-the-results" />

### ステップ4. 結果を分析する

分析ステップは、通常、測定誤差の軽減やゼロノイズ外挿（ZNE）などを使用して結果を後処理する場所である。 これらの結果をさらに分析するために別のワークフローに送り込んだり、キーとなる値やデータのプロットを作成することもできる。 一般的に、このステップはあなたの問題に特化したものである。  この例では、回路について測定された各期待値をプロットする。

Estimatorに指定した観測値の期待値と標準偏差は、ジョブ結果の `PubResult.data.evs` と `PubResult.data.stds` 属性からアクセスできます。 Samplerから結果を得るには、 `PubResult.data.meas.get_counts()` 関数を使用する。 関数は、ビット列をキー、カウント数を対応する値として、 `dict` 形式の測定値を返す。 詳しくは[サンプラーを始めようをご覧ください。](/docs/guides/get-started-with-primitives#get-started-with-sampler)



In [7]:
# Plot the result

from matplotlib import pyplot as plt

values = pub_result.data.evs

errors = pub_result.data.stds

# plotting graph
plt.plot(observables_labels, values, "-o")
plt.xlabel("Observables")
plt.ylabel("Values")
plt.show()

<Image src="/docs/images/tutorials/hello-world/extracted-outputs/87143fcc-0.svg" alt="Output of the previous code cell" />

量子ビット0と1の場合、XとZの独立した期待値は0であり、相関（`XX` と `ZZ` ）は1である。 これは量子もつれの特徴である。



<span id="scale-to-large-numbers-of-qubits" />

## 大量の量子ビットに拡張可能

量子コンピューティングでは、実用規模の研究がこの分野の進歩に不可欠である。 このような仕事では、100以上の量子ビットと1000以上のゲートを使うような回路を使って、はるかに大規模な計算を行う必要がある。 この例では、 IBM® QPUで100量子ビットのGHZステートを作成し解析することで、ユーティリティ・スケールの作業を達成できることを示しています。  Qiskitパターンのワークフローを使用し、各クビットの期待値（ $\langle Z_0 Z_i \rangle $ ）を測定することで終了する。

<span id="step-1-map-the-problem" />

### ステップ1. 問題の地図

$n$ -qubitのGHZ状態（基本的には拡張ベル状態）を準備する `QuantumCircuit` を返す関数を書き、その関数を使用して100qubitのGHZ状態を準備し、測定する観測量を収集する。



In [9]:
from qiskit import QuantumCircuit


def get_qc_for_n_qubit_GHZ_state(n: int) -> QuantumCircuit:
    """This function will create a qiskit.QuantumCircuit (qc) for an n-qubit GHZ state.

    Args:
        n (int): Number of qubits in the n-qubit GHZ state

    Returns:
        QuantumCircuit: Quantum circuit that generate the n-qubit GHZ state, assuming all qubits start in the 0 state
    """
    if isinstance(n, int) and n >= 2:
        qc = QuantumCircuit(n)
        qc.h(0)
        for i in range(n - 1):
            qc.cx(i, i + 1)
    else:
        raise Exception("n is not a valid input")
    return qc


# Create a new circuit with two qubits (first argument) and two classical
# bits (second argument)
n = 100
qc = get_qc_for_n_qubit_GHZ_state(n)

次に、関心のあるオペレーターにマップを作成する。 この例では、量子ビット間の演算子（ `ZZ` ）を使って、量子ビットが離れていくときの挙動を調べている。  離れた量子ビット間の期待値が不正確（破損）になればなるほど、存在するノイズのレベルが明らかになる。



In [10]:
from qiskit.quantum_info import SparsePauliOp

# ZZII...II, ZIZI...II, ... , ZIII...IZ
operator_strings = [
    "Z" + "I" * i + "Z" + "I" * (n - 2 - i) for i in range(n - 1)
]
print(operator_strings)
print(len(operator_strings))

operators = [SparsePauliOp(operator) for operator in operator_strings]

['ZZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII', 'ZIZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII', 'ZIIZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII', 'ZIIIZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII', 'ZIIIIZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII', 'ZIIIIIZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII', 'ZIIIIIIZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII', 'ZIIIIIIIZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII', 'ZIIIIIIIIZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII', 'ZIIIIIIIIIZIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIIII

<span id="step-2-optimize-the-problem-for-execution-on-quantum-hardware" />

### ステップ2. 量子ハードウェア上で実行できるように問題を最適化する

以下のコードは、バックエンドのISAに合わせて回路とobservablesを変換する。 [認証情報を保存して](/docs/guides/cloud-setup)いる必要があります



In [11]:
from qiskit.transpiler import generate_preset_pass_manager
from qiskit_ibm_runtime import QiskitRuntimeService

service = QiskitRuntimeService()

backend = service.least_busy(
    simulator=False, operational=True, min_num_qubits=100
)
pm = generate_preset_pass_manager(optimization_level=1, backend=backend)

isa_circuit = pm.run(qc)
isa_operators_list = [op.apply_layout(isa_circuit.layout) for op in operators]

<span id="step-3-execute-on-hardware" />

### ステップ3． ハードウェア上での実行

ジョブを投入し、 [ダイナミック・デカップリングと](../api/qiskit-ibm-runtime/options-dynamical-decoupling-options)呼ばれるエラー削減テクニックを使ってエラー抑制を有効にする レジリエンス・レベルは、エラーに対してどの程度の回復力を持たせるかを指定する。 レベルが高いほど正確な結果が得られるが、その代償として処理時間が長くなる。  以下のコードで設定されるオプションの詳細については、 [Qiskit Runtime のエラー緩和を設定する](/docs/guides/configure-error-mitigation)を参照のこと



In [12]:
from qiskit_ibm_runtime import EstimatorOptions
from qiskit_ibm_runtime import EstimatorV2 as Estimator

options = EstimatorOptions()
options.resilience_level = 1
options.dynamical_decoupling.enable = True
options.dynamical_decoupling.sequence_type = "XY4"

# Create an Estimator object
estimator = Estimator(backend, options=options)

In [13]:
# Submit the circuit to Estimator
job = estimator.run([(isa_circuit, isa_operators_list)])
job_id = job.job_id()
print(job_id)

d2qkqt9olshc73bmb9g0


<span id="step-4-post-process-results" />

### ステップ4. ポスト・プロセス結果

ジョブが完了した後、結果をプロットしてください。理想的なシミュレーションでは、すべての $\langle Z_0 Z_i \rangle$ が1になるはずですが、 $i$ が増加するにつれて、 $\langle Z_0 Z_i \rangle$ が減少していることに注目してください。



In [14]:
import matplotlib.pyplot as plt
from qiskit_ibm_runtime import QiskitRuntimeService

# data
data = list(range(1, len(operators) + 1))  # Distance between the Z operators
result = job.result()[0]
values = result.data.evs  # Expectation value at each Z operator.
values = [
    v / values[0] for v in values
]  # Normalize the expectation values to evaluate how they decay with distance.

# plotting graph
plt.plot(data, values, marker="o", label="100-qubit GHZ state")
plt.xlabel("Distance between qubits $i$")
plt.ylabel(r"$\langle Z_i Z_0 \rangle / \langle Z_1 Z_0 \rangle $")
plt.legend()
plt.show()

<Image src="/docs/images/tutorials/hello-world/extracted-outputs/de91ebd0-0.svg" alt="Output of the previous code cell" />

先のプロットは、量子ビット間の距離が長くなるにつれて、ノイズの存在により信号が減衰することを示している。



<span id="next-steps" />

## 次のステップ

<Admonition type="tip" title="推奨事項">
  *   [回路の作り方を](/docs/guides/map-problem-to-circuits)より詳しく学ぶ。
  *   [VQEチュートリアルによるハイゼンベルグ鎖の基底状態エネルギー推定を](/docs/tutorials/spin-chain-vqe)お試しください。
</Admonition>



© IBM Corp., 2017-2025